In [8]:
import pandas as pd
from geopy.geocoders import Nominatim
from datetime import datetime
import numpy as np


In [9]:
df_bundesland_all = pd.read_csv('df_bundesland_all.csv')

In [10]:
df_bundesland_all.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 473619 entries, 0 to 473618
Data columns (total 30 columns):
 #   Column                  Non-Null Count   Dtype  
---  ------                  --------------   -----  
 0   Unnamed: 0.1            473619 non-null  int64  
 1   Unnamed: 0              473619 non-null  int64  
 2   ANO_SID                 473618 non-null  float64
 3   CORPORATE_DEVISION      473619 non-null  object 
 4   ORTPLZ                  473619 non-null  int64  
 5   ORTS-NAME               473618 non-null  object 
 6   STRASSE                 473475 non-null  object 
 7   SUM_INSURED             472946 non-null  float64
 8   CONSTRACTION_DESIGN     426373 non-null  object 
 9   CONSTRUCTION_YEAR       473619 non-null  float64
 10  WFL                     472941 non-null  float64
 11  ZONE                    451263 non-null  object 
 12  SF-SYSTEM               81284 non-null   float64
 13  TYPE_OF_DEDUCTIBLE      473619 non-null  int64  
 14  DRAIN_PIPE_INSURED  

In [11]:
# Nach Bundesland sortieren
df_bundesland_all = df_bundesland_all.sort_values(by='Bundesland')

# Anzahl der Einträge pro Bundesland berechnen
bundesland_counts = df_bundesland_all['Bundesland'].value_counts().sort_index()

# Ergebnis anzeigen
print(bundesland_counts)

# Optional: Ausgabe in einem DataFrame speichern
df_bundesland_counts = bundesland_counts.reset_index()
df_bundesland_counts.columns = ['Bundesland', 'Anzahl Einträge']

print(df_bundesland_counts)

Bundesland
Baden-Württemberg          57676
Bayern                     70309
Berlin                      8645
Brandenburg                15616
Bremen                      2993
Hamburg                     6468
Hessen                     35676
Mecklenburg-Vorpommern     11384
Niedersachsen              58934
Nordrhein-Westfalen       110549
Rheinland-Pfalz            28617
Saarland                    4226
Sachsen                    18276
Sachsen-Anhalt             11209
Schleswig-Holstein         18511
Thüringen                  14530
Name: count, dtype: int64
                Bundesland  Anzahl Einträge
0        Baden-Württemberg            57676
1                   Bayern            70309
2                   Berlin             8645
3              Brandenburg            15616
4                   Bremen             2993
5                  Hamburg             6468
6                   Hessen            35676
7   Mecklenburg-Vorpommern            11384
8            Niedersachsen            5

In [1]:
df_bundesland_all = df_bundesland_all[
    (df_bundesland_all['Bundesland'] != 'Bayern') &
    (df_bundesland_all['Bundesland'] != 'Baden-Württemberg') &
    (df_bundesland_all['Bundesland'] != 'Berlin') &
    (df_bundesland_all['Bundesland'] != 'Brandenburg') &
    (df_bundesland_all['Bundesland'] != 'Bremen') &
    (df_bundesland_all['Bundesland'] != 'Hamburg') &
    (df_bundesland_all['Bundesland'] != 'Hessen') &
    (df_bundesland_all['Bundesland'] != 'Mecklenburg-Vorpommern') &
    (df_bundesland_all['Bundesland'] != 'Niedersachsen') &
    (df_bundesland_all['Bundesland'] != 'Nordrhein-Westfalen') &
    (df_bundesland_all['Bundesland'] != 'Saarland') &
    (df_bundesland_all['Bundesland'] != 'Rheinland-Pfalz') &
    (df_bundesland_all['Bundesland'] != 'Sachsen') &
    (df_bundesland_all['Bundesland'] != 'Sachsen-Anhalt') &
    (df_bundesland_all['Bundesland'] != 'Schleswig-Holstein') &
    (df_bundesland_all['Bundesland'] != 'Thüringen')

]


SyntaxError: invalid syntax (307773843.py, line 15)

In [6]:
import pandas as pd
import numpy as np
from geopy.geocoders import Nominatim
from datetime import datetime

# DataFrame df_bundesland_all verwenden
df_all = df_bundesland_all.copy()

# Zähler für die Gesamtzahl der Geokodierungen
total_count = 0

# Funktion zur Geokodierung basierend auf der ORTPLZ und der STRASSE
geolocator = Nominatim(user_agent="CapStone")

def get_coordinates(row, count):
    global total_count
    try:
        location = geolocator.geocode(f"{row['ORTPLZ']}, {row['STRASSE']}, Germany")
        if location:
            timestamp = datetime.now().strftime("%Y-%m-%d %H:%M:%S")
            total_count += 1
            print(f"{total_count}: Geokodierung erfolgreich für ANO_SID: {row['ANO_SID']} - Bundesland: {row['Bundesland']} - ORTPLZ: {row['ORTPLZ']} - STRASSE: {row['STRASSE']} - Latitude: {location.latitude}, Longitude: {location.longitude} - Zeitstempel: {timestamp}")
            count += 1
            return location.latitude, location.longitude, count
        else:
            timestamp = datetime.now().strftime("%Y-%m-%d %H:%M:%S")
            total_count += 1
            print(f"{total_count}: Keine Koordinaten gefunden für ANO_SID: {row['ANO_SID']} - Bundesland: {row['Bundesland']} - ORTPLZ: {row['ORTPLZ']} - STRASSE: {row['STRASSE']} - Zeitstempel: {timestamp}")
            count += 1
            return None, None, count
    except Exception as e:
        timestamp = datetime.now().strftime("%Y-%m-%d %H:%M:%S")
        total_count += 1
        print(f"{total_count}: Fehler bei ANO_SID: {row['ANO_SID']} - Bundesland: {row['Bundesland']} - ORTPLZ: {row['ORTPLZ']} - STRASSE: {row['STRASSE']} - Fehler: {e} - Zeitstempel: {timestamp}")
        count += 1
        return None, None, count

def split_and_save_nrw(subset, part):
    count = 0
    latitude = []
    longitude = []
    for index, row in subset.iterrows():
        lat, lon, count = get_coordinates(row, count)
        latitude.append(lat)
        longitude.append(lon)
    
    subset['LATITUDE'] = latitude
    subset['LONGITUDE'] = longitude
    
    # Speichern des aktualisierten Subsets
    try:
        subset.to_csv(f'coord_subset_Nordrhein-Westfalen-{part}.csv', index=False)
        print(f'Subset für Nordrhein-Westfalen-{part} gespeichert als coord_subset_Nordrhein-Westfalen-{part}.csv')
    except Exception as e:
        print(f"Fehler beim Speichern des Subsets für Nordrhein-Westfalen-{part}: ANO_SID: {row['ANO_SID']} - ORTPLZ: {row['ORTPLZ']} - STRASSE: {row['STRASSE']} - Fehler: {e}")

# Gruppierung des DataFrames nach 'Bundesland'
grouped_bundesland = df_all.groupby('Bundesland')

# Geokodierung und Speichern der Subsets
for bundesland, subset in grouped_bundesland:
    if bundesland == 'Nordrhein-Westfalen':
        # Split into three parts
        subsets = np.array_split(subset, 3)
        # Only process and save the third subset
        split_and_save_nrw(subsets[2], 3)
    else:
        count = 0
        latitude = []
        longitude = []
        for index, row in subset.iterrows():
            lat, lon, count = get_coordinates(row, count)
            latitude.append(lat)
            longitude.append(lon)
        
        subset['LATITUDE'] = latitude
        subset['LONGITUDE'] = longitude
        
        # Speichern des aktualisierten Subsets
        try:
            subset.to_csv(f'coord_subset_{bundesland}.csv', index=False)
            print(f'Subset für Bundesland {bundesland} gespeichert als coord_subset_{bundesland}.csv')
        except Exception as e:
            print(f"Fehler beim Speichern des Subsets für Bundesland {bundesland}: ANO_SID: {row['ANO_SID']} - ORTPLZ: {row['ORTPLZ']} - STRASSE: {row['STRASSE']} - Fehler: {e}")


1: Geokodierung erfolgreich für ANO_SID: 49196504.0 - Bundesland: Sachsen - ORTPLZ: 1067 - STRASSE: Adlergasse - Latitude: 48.823641, Longitude: 9.9193435 - Zeitstempel: 2024-06-12 14:38:22
2: Geokodierung erfolgreich für ANO_SID: 57988375.0 - Bundesland: Sachsen - ORTPLZ: 8058 - STRASSE: Hospitalstr. - Latitude: 49.7850836, Longitude: 6.5373485 - Zeitstempel: 2024-06-12 14:38:24
3: Geokodierung erfolgreich für ANO_SID: 143503818.0 - Bundesland: Sachsen - ORTPLZ: 4849 - STRASSE: Görschlitzer Weg - Latitude: 51.6149474, Longitude: 12.6753708 - Zeitstempel: 2024-06-12 14:38:24
4: Geokodierung erfolgreich für ANO_SID: 58264660.0 - Bundesland: Sachsen - ORTPLZ: 4849 - STRASSE: Hauptstr. - Latitude: 49.5098493, Longitude: 12.5481547 - Zeitstempel: 2024-06-12 14:38:25
5: Geokodierung erfolgreich für ANO_SID: 58140646.0 - Bundesland: Sachsen - ORTPLZ: 4849 - STRASSE: Heidering - Latitude: 52.26522455, Longitude: 8.317467469567784 - Zeitstempel: 2024-06-12 14:38:25
6: Fehler bei ANO_SID: 55266